# BayesExpert Marketplace Demo

The BayesExpert Marketplace Demo will allow the user to input any of the Bayesian nets in a list or uploaded from their disk.The python code uploaded from their disk should be in the same form that the longevity_bayes.py net is, including routines like addCPT.  The py code should generate a protobuf message file, which bayesInitialize will convert to a pomegranate file, which must be baked before queried.  The four text windows in the top of the GUI show the text descripton of the net for the user to read, the python code of the net, the human readable form of the net, and the pomegranate form of the net.  The compiled code will be preloaded for our nets in a pickle file like bayesianNetwork.pkl, but for the uploaded net, we will call their code to show them the compiled form of the net, and then call readable to show them the readable form of their code, then call baked before entering a query. For the pre-available nets, there will be a directory that contains the needed files. Below we show how each window is generated for a net that is a "user supplied" net.


Example:  The user selects upload from the left hand dial, and the text appears in the upper text box:


"Upload a BayesExpert Bayesian network, then see and query the Bayesian Network it creates.  The Rejuve.AI website also has a Graphical User Interface that generates a BayesExpert Bayesian network, for your convenience." 


The user then uploads the following code, at which point a complexity check is done on it before it is called.  Also there are safety features that prevent the calling of any python code.  Upon calling, all three text windows below the top wndow are immediately filled in as follows:

The code generator on the website will be able to generate such code, plus the user can copy over and paste code from another short network. Say the following cell is the code that the user uploads.    It would appear in the "python code" window.

In [1]:
# complexity check and ensure not hackable

In [2]:
import sn_bayes
from sn_bayes.utils import any_of
from sn_bayes.utils import all_of
from sn_bayes.utils import avg
from sn_bayes.utils import if_then_else
from sn_bayes.utils import addCpt
from sn_bayes.utils import dependency
from sn_bayes.utils import non_cpt_descriptions

import sn_service.service_spec.bayesian_pb2
from sn_service.service_spec.bayesian_pb2 import BayesianNetwork

bayesianNetwork = BayesianNetwork()
cpt = {}
outstr = '' 


discreteDistribution = bayesianNetwork.discreteDistributions.add()
discreteDistribution.name = "gender"
variable = discreteDistribution.variables.add()
variable.name = "male"
variable.probability = 0.49
variable = discreteDistribution.variables.add()
variable.name = "female"
variable.probability = 0.51

discreteDistribution = bayesianNetwork.discreteDistributions.add()
discreteDistribution.name = "cotinine"
variable = discreteDistribution.variables.add()
variable.name = "cotinine_above_323.00"
variable.probability = 0.05
variable = discreteDistribution.variables.add()
variable.name = "cotinine_above_1.01_to_323.00_and_below"
variable.probability = 0.20
variable = discreteDistribution.variables.add()
variable.name = "cotinine_above_0.03_to_1.01_and_below"
variable.probability = 0.25
variable = discreteDistribution.variables.add()
variable.name = "cotinine_above_0.01_to_0.03_and_below"
variable.probability = 0.25
variable = discreteDistribution.variables.add()
variable.name = "cotinine_0.01_and_below"
variable.probability = 0.25


discreteDistribution = bayesianNetwork.discreteDistributions.add()
discreteDistribution.name = "second_hand_smoke"
variable = discreteDistribution.variables.add()
variable.name = "second_hand_smoke_yes"
variable.probability = 0.31
variable = discreteDistribution.variables.add()
variable.name = "second_hand_smoke_no"
variable.probability = 0.69


discreteDistribution = bayesianNetwork.discreteDistributions.add()
discreteDistribution.name = "five_days_smoke_cigarettes"
variable = discreteDistribution.variables.add()
variable.name = "five_days_smoke_cigarettes_yes"
variable.probability = 0.19
variable = discreteDistribution.variables.add()
variable.name = "five_days_smoke_cigarettes_no"
variable.probability = 0.81

discreteDistribution = bayesianNetwork.discreteDistributions.add()
discreteDistribution.name = "ever_vaped"
variable = discreteDistribution.variables.add()
variable.name = "ever_vaped_yes"
variable.probability = 0.20
variable = discreteDistribution.variables.add()
variable.name = "ever_vaped_no"
variable.probability = 0.80



cpt["smoking"] = avg(bayesianNetwork,cpt,
 [
 "second_hand_smoke",
 "five_days_smoke_cigarettes",
 "ever_vaped",
 "cotinine"
 ],
 ["smoking","no_smoking"]
 )



outstr = outstr + addCpt(bayesianNetwork,cpt)
cpt = {}


cpt["hallmark_2_telomere_attrition"] = dependency(bayesianNetwork,cpt,
        [
            ({"smoking":["no_smoking"]},{"relative_risk":0.8194679424, "plus_minus": 0.07426312427, "ci": 95}),
            ({"gender":["male"]},{"relative_risk":1.176918992, "plus_minus": 0.1495149128, "ci": 95}),
        ],
        {"hallmark_2_telomere_attrition":0.1, "no_hallmark_2_telomere_attrition":0.9}
        )

outstr = outstr + addCpt(bayesianNetwork,cpt)
cpt = {}



cpt["obstructive_sleep_apnea"] = dependency(bayesianNetwork,cpt,
        [
            ({"hallmark_2_telomere_attrition":["no_hallmark_2_telomere_attrition"]},{"relative_risk":.06})
        ],
        {"obstructive_sleep_apnea":0.150, "no_obstructive_sleep_apnea":0.85}
        )


outstr = outstr + addCpt(bayesianNetwork,cpt)


start timing...
start timing...
[({'smoking': ['no_smoking']}, {'relative_risk': 0.8194679424, 'plus_minus': 0.07426312427, 'ci': 95}), ({'always_true': ['always_true']}, {'relative_risk': 1.0})] ==> {'hallmark_2_telomere_attrition': 0.1, 'no_hallmark_2_telomere_attrition': 0.9} took 0.03571666099924187 seconds
start timing...
[({'gender': ['male']}, {'relative_risk': 1.176918992, 'plus_minus': 0.1495149128, 'ci': 95}), ({'always_true': ['always_true']}, {'relative_risk': 1.0})] ==> {'hallmark_2_telomere_attrition': 0.1, 'no_hallmark_2_telomere_attrition': 0.9} took 0.03476118099933956 seconds
start timing...
[({'smoking': ['no_smoking']}, {'relative_risk': 0.8194679424, 'plus_minus': 0.07426312427, 'ci': 95}), ({'gender': ['male']}, {'relative_risk': 1.176918992, 'plus_minus': 0.1495149128, 'ci': 95})] ==> {'hallmark_2_telomere_attrition': 0.1, 'no_hallmark_2_telomere_attrition': 0.9} took 0.029153948000384844 seconds
{'hallmark_2_telomere_attrition': 0.1, 'no_hallmark_2_telomere_attr

/usr/local/lib/python3.6/dist-packages/qpsolvers/solvers/typing.py:49: UserWarning: Converted P to scipy.sparse.csc.csc_matrix
For best performance, build P as a scipy.sparse.csc_matrix rather than as a numpy.ndarray
  f"Converted {matrix_name} to scipy.sparse.csc.csc_matrix\n"
/usr/local/lib/python3.6/dist-packages/qpsolvers/solvers/typing.py:49: UserWarning: Converted A to scipy.sparse.csc.csc_matrix
For best performance, build A as a scipy.sparse.csc_matrix rather than as a numpy.ndarray
  f"Converted {matrix_name} to scipy.sparse.csc.csc_matrix\n"


The user's uploaded code above also has human readable output, then is generated when it is called.  That output is to be displayed in the second window, titled "human readable".

In [3]:
print(outstr)

smoking has the value of smoking if the values of second_hand_smoke and five_days_smoke_cigarettes and ever_vaped and cotinine average to the highest level of risk. smoking has the value of no_smoking if the values of second_hand_smoke and five_days_smoke_cigarettes and ever_vaped and cotinine average to the next highest level of risk. 

Against the baseline risks, the relative risk that hallmark_2_telomere_attrition will be hallmark_2_telomere_attrition for those in the smoking category of no_smoking is 0.8194679424 , the plus minus that hallmark_2_telomere_attrition will be hallmark_2_telomere_attrition for those in the smoking category of no_smoking is 0.07426312427 , the ci that hallmark_2_telomere_attrition will be hallmark_2_telomere_attrition for those in the smoking category of no_smoking is 95 , the relative risk that hallmark_2_telomere_attrition will be hallmark_2_telomere_attrition for those in the gender category of male is 1.176918992 , the plus minus that hallmark_2_telo

The user's uploaded code creates a protobuf message, above in the variable "bayesianNetwork".  We show the protobuf version in the third window, "compiled code"

In [4]:
print(bayesianNetwork)

discreteDistributions {
  name: "gender"
  variables {
    name: "male"
    probability: 0.49000000953674316
  }
  variables {
    name: "female"
    probability: 0.5099999904632568
  }
}
discreteDistributions {
  name: "cotinine"
  variables {
    name: "cotinine_above_323.00"
    probability: 0.05000000074505806
  }
  variables {
    name: "cotinine_above_1.01_to_323.00_and_below"
    probability: 0.20000000298023224
  }
  variables {
    name: "cotinine_above_0.03_to_1.01_and_below"
    probability: 0.25
  }
  variables {
    name: "cotinine_above_0.01_to_0.03_and_below"
    probability: 0.25
  }
  variables {
    name: "cotinine_0.01_and_below"
    probability: 0.25
  }
}
discreteDistributions {
  name: "second_hand_smoke"
  variables {
    name: "second_hand_smoke_yes"
    probability: 0.3100000023841858
  }
  variables {
    name: "second_hand_smoke_no"
    probability: 0.6899999976158142
  }
}
discreteDistributions {
  name: "five_days_smoke_cigarettes"
  variables {
    name: "

The above applies to user uploaded files, however, there will be a directory containing the content of the three windows for the precompiled nets that we are offerring, called <netname>.py for the python code, <netname>_human_readable.txt for the human readable code, and <netname>_protobuf.txt for the compiled code to go in the first second and third windows respectively.  However, whether the net is uploaded or precompiled, the protobuf net is sent to the service as a message and is queried in the same step with the stateless function.  For the uploaded nets, the protobuf is formed by calling the code, but for the nets that we offer, the protobuf is in the pickle file, named <netname>.pkl.  The code below calls the stateless function on the protobuf message from either source.

In preparing the net for query, all of the nodes of the net are included in the output, except if there is a file present called <netname>_output.txt which lists the variables for the output, one per line. This may be present for the longevity_bayes net, in which case, the file would contain the hallmark variables.  Below we simply include all nodes, obtained from the function var_positions:

In [5]:
import sn_bayes
from sn_bayes.utils import get_var_positions
var_positions = get_var_positions(bayesianNetwork)
list_of_variables = list(var_positions.keys())
list_of_variables

['gender',
 'cotinine',
 'second_hand_smoke',
 'five_days_smoke_cigarettes',
 'ever_vaped',
 'smoking',
 'hallmark_2_telomere_attrition',
 'obstructive_sleep_apnea']

Using the variable value windows in the middle of the form, and the "add evidence" button, the user adds evidence.  Say they add the following evidence:

In [6]:
evidence = {"ever_vaped":"ever_vaped_yes"}

When the calculate button is pressed, the outvars and evidence are added to the protobuf message, and the message is sent to the service.  The query answers are put into the probabilities window, after converted back from numbers to variable names

In [7]:
import sn_bayes
from sn_bayes.utils import get_var_val_positions
import sn_service.service_spec.bayesian_pb2
from sn_service.service_spec.bayesian_pb2 import Query

var_val_positions = get_var_val_positions(bayesianNetwork)
query = Query()
query.switch = "internal_query"

for v in list_of_variables:
    if v in var_positions:
        outvar = query.include_list.add()
        outvar.var_num = var_positions[v]
for var,val  in  evidence.items():
    e= query.evidence.add()
    e.var_num = var_positions[var] if var in var_positions else 0
    e.response = var_val_positions[var][val] if var in var_positions and val in var_val_positions[var] else 0
for o in list_of_variables:
    outvar = query.outvars.add()
    outvar.var_num = var_positions[o] if o in var_positions else 0


In [11]:
from sn_bayes.utils import create_query
import grpc
import sn_service.service_spec.bayesian_pb2_grpc as grpc_bayes_grpc
import sn_service.service_spec.bayesian_pb2
from sn_service.service_spec.bayesian_pb2 import BayesianNetworkQuery
from sn_service.service_spec.bayesian_pb2 import QueryId
from sn_service.service_spec.bayesian_pb2 import Id

endpoint = "localhost:7003"
channel = grpc.insecure_channel("{}".format(endpoint))
stub = grpc_bayes_grpc.BayesNetStub(channel)

bayesianNetworkQuery = BayesianNetworkQuery()
bayesianNetworkQuery.query.CopyFrom(query)
bayesianNetworkQuery.bayesianNetwork.CopyFrom(bayesianNetwork)
print (bayesianNetworkQuery)
print ("Calling StatelessNet")

%time response = stub.StatelessNet(bayesianNetworkQuery)
print("response.varAnswers")
print(response.varAnswers)
print("response.error_msg")
print(response.error_msg)

bayesianNetwork {
  discreteDistributions {
    name: "gender"
    variables {
      name: "male"
      probability: 0.49000000953674316
    }
    variables {
      name: "female"
      probability: 0.5099999904632568
    }
  }
  discreteDistributions {
    name: "cotinine"
    variables {
      name: "cotinine_above_323.00"
      probability: 0.05000000074505806
    }
    variables {
      name: "cotinine_above_1.01_to_323.00_and_below"
      probability: 0.20000000298023224
    }
    variables {
      name: "cotinine_above_0.03_to_1.01_and_below"
      probability: 0.25
    }
    variables {
      name: "cotinine_above_0.01_to_0.03_and_below"
      probability: 0.25
    }
    variables {
      name: "cotinine_0.01_and_below"
      probability: 0.25
    }
  }
  discreteDistributions {
    name: "second_hand_smoke"
    variables {
      name: "second_hand_smoke_yes"
      probability: 0.3100000023841858
    }
    variables {
      name: "second_hand_smoke_no"
      probability: 0.68999